In [13]:
import pandas as pd
import plotly.express as px
import requests
import io

def clean_data(df):
    """
    Cleans the DataFrame by handling data types and missing values for key columns.
    """
    # It now checks for the standardized, lowercase column names.
    required_cols = ['price', 'neighbourhood_group', 'room_type', 'host_name']

    for col in required_cols:
        if col not in df.columns:
            print(f"❌ Critical column '{col}' not found after standardization. Analysis cannot proceed.")
            return pd.DataFrame()

    # Clean numeric columns robustly, converting non-numeric entries to NaN
    df['price'] = pd.to_numeric(df['price'], errors='coerce')

    optional_numeric_cols = ['service_fee', 'construction_year', 'number_of_reviews']
    for col in optional_numeric_cols:
        if col in df.columns:
            df[col] = pd.to_numeric(df[col], errors='coerce')

    # Drop rows where essential information is missing
    df.dropna(subset=required_cols, inplace=True)

    if df.empty:
        print("⚠️ DataFrame is empty after cleaning.")
        return pd.DataFrame()

    print("✅ Data cleaning complete.")
    return df

def plot_q1_property_types(df):
    """Analyzes and visualizes the distribution of property types."""
    try:
        if 'room_type' not in df.columns: raise ValueError("'room_type' column is missing.")
        data = df['room_type'].value_counts().reset_index()
        data.columns = ['Room Type', 'Count']
        fig = px.pie(data, names='Room Type', values='Count',
                     title="<b>Distribution of Property Types</b>",
                     hole=0.3)
        fig.update_traces(hovertemplate='<b>%{label}</b><br>Listings: %{value}<br>Percentage: %{percent}')
        fig.update_layout(title_x=0.5)
        fig.show()
    except Exception as e:
        print(f"Failed to generate plot for Question 1: {e}")

def plot_q2_top_neighborhoods(df):
    """Analyzes and visualizes the number of listings per neighborhood group."""
    try:
        if 'neighbourhood_group' not in df.columns: raise ValueError("'neighbourhood_group' column is missing.")
        data = df['neighbourhood_group'].value_counts().reset_index()
        data.columns = ['Neighborhood Group', 'Number of Listings']
        fig = px.bar(data,
                     x='Number of Listings',
                     y='Neighborhood Group',
                     orientation='h',
                     title="<b>Number of Listings by Neighborhood Group</b>",
                     color='Number of Listings',
                     labels={'Number of Listings': 'Total Number of Listings', 'Neighborhood Group': 'Neighborhood Group'})
        fig.update_layout(yaxis={'categoryorder':'total ascending'}, title_x=0.5)
        fig.show()
    except Exception as e:
        print(f"Failed to generate plot for Question 2: {e}")

def plot_q3_avg_price_by_neighborhood(df):
    """Analyzes and visualizes the average price by neighborhood group."""
    try:
        if not all(c in df.columns for c in ['neighbourhood_group', 'price']): raise ValueError("Required columns for Question 3 are missing.")
        data = df.groupby('neighbourhood_group')['price'].mean().reset_index().sort_values('price', ascending=False)
        fig = px.bar(data,
                     x='neighbourhood_group',
                     y='price',
                     title="<b>Average Listing Price by Neighborhood Group</b>",
                     labels={'neighbourhood_group': 'Neighborhood Group', 'price': 'Average Price ($)'},
                     color='price',
                     color_continuous_scale='Plasma')
        fig.update_traces(hovertemplate='<b>%{x}</b><br>Average Price: $%{y:.2f}<extra></extra>')
        fig.update_layout(title_x=0.5)
        fig.show()
    except Exception as e:
        print(f"Failed to generate plot for Question 3: {e}")

def plot_q4_year_vs_price(df):
    """Robustly analyzes the relationship between construction year and price."""
    try:
        required = ['construction_year', 'price']
        if not all(c in df.columns for c in required):
            raise ValueError("One or more required columns ('construction_year', 'price') are missing.")
        df_work = df[required].dropna()
        if df_work.empty:
            raise ValueError("There are no rows with valid data for both 'construction year' and 'price'.")
        price_cap = df_work['price'].quantile(0.99)
        df_filtered = df_work[df_work['price'] < price_cap]
        if df_filtered.empty or len(df_filtered) < 2:
             raise ValueError(f"Not enough valid data points remain after filtering price outliers (cap: ${price_cap:.2f}).")

        print(f"Analyzing {len(df_filtered)} listings for Question 4...")
        fig = px.scatter(df_filtered,
                         x='construction_year',
                         y='price',
                         title="<b>Price vs. Construction Year Relationship</b>",
                         labels={'construction_year': 'Construction Year', 'price': 'Price ($)'},
                         opacity=0.5,
                         trendline="ols",
                         trendline_color_override="red")
        fig.update_traces(hovertemplate='<b>Year:</b> %{x}<br><b>Price:</b> $%{y:.2f}<extra></extra>')
        fig.update_layout(title_x=0.5)
        fig.show()
    except Exception as e:
        print(f"⚠️ Failed to generate plot for Question 4: {e}")

def plot_q5_top_hosts(df):
    """Analyzes and visualizes the top 10 hosts by listing count."""
    try:
        if 'host_name' not in df.columns: raise ValueError("'host_name' column is missing.")
        data = df['host_name'].value_counts().nlargest(10).reset_index()
        data.columns = ['Host Name', 'Listing Count']
        fig = px.bar(data,
                     x='Listing Count',
                     y='Host Name',
                     orientation='h',
                     title="<b>Top 10 Hosts by Number of Listings</b>",
                     labels={'Listing Count': 'Number of Properties Listed', 'Host Name': 'Host Name'},
                     color='Listing Count',
                     text='Listing Count')
        fig.update_layout(yaxis={'categoryorder':'total ascending'}, title_x=0.5)
        fig.update_traces(textposition='outside')
        fig.show()
    except Exception as e:
        print(f"Failed to generate plot for Question 5: {e}")

def plot_q6_verified_vs_reviews(df):
    """Analyzes and visualizes the impact of host verification on reviews."""
    try:
        if not all(c in df.columns for c in ['host_identity_verified', 'number_of_reviews']): raise ValueError("Required columns for Question 6 are missing.")
        data = df.dropna(subset=['host_identity_verified', 'number_of_reviews']).groupby('host_identity_verified')['number_of_reviews'].mean().reset_index()
        if data.empty: raise ValueError("No valid data for verified vs. reviews analysis.")
        fig = px.bar(data,
                     x='host_identity_verified',
                     y='number_of_reviews',
                     title='<b>Average Reviews for Verified vs. Unverified Hosts</b>',
                     labels={'host_identity_verified': 'Host Identity Status', 'number_of_reviews': 'Average Number of Reviews'},
                     color='host_identity_verified',
                     color_discrete_map={'unconfirmed': 'orange', 'verified': 'green'})
        fig.update_layout(legend_title_text='Verification Status', title_x=0.5)
        fig.show()
    except Exception as e:
        print(f"Failed to generate plot for Question 6: {e}")

def plot_q7_price_vs_fee(df):
    """Analyzes and visualizes the correlation between price and service fee."""
    try:
        if not all(c in df.columns for c in ['price', 'service_fee']): raise ValueError("Required columns for Question 7 are missing.")
        df_filtered = df.dropna(subset=['price', 'service_fee'])
        if df_filtered.empty: raise ValueError("No valid data for price vs. service fee analysis.")
        correlation = df_filtered['price'].corr(df_filtered['service_fee'])
        print(f"The correlation between price and service fee is: {correlation:.2f}")
        fig = px.scatter(df_filtered,
                         x='price',
                         y='service_fee',
                         title=f"<b>Price vs. Service Fee (Correlation: {correlation:.2f})</b>",
                         labels={'price': 'Listing Price ($)', 'service_fee': 'Service Fee ($)'},
                         opacity=0.5,
                         trendline="ols",
                         trendline_color_override="red")
        fig.update_traces(hovertemplate='<b>Price:</b> $%{x:.2f}<br><b>Service Fee:</b> $%{y:.2f}<extra></extra>')
        fig.update_layout(title_x=0.5)
        fig.show()
    except Exception as e:
        print(f"Failed to generate plot for Question 7: {e}")

def main():
    """
    Main function to run the complete analysis pipeline.
    """
    # --- 1. PASTE THE RAW GITHUB URL FOR YOUR EXCEL (.xlsx) FILE HERE ---
    url = 'https://github.com/Nishant17s/VOIS_AICTE_Oct2025_NISHANT/raw/refs/heads/main/1730285881-Airbnb_Open_Data%20(3).xlsx'

    try:
        response = requests.get(url)
        response.raise_for_status()
        df_raw = pd.read_excel(io.BytesIO(response.content))

        # --- 2. THIS PRINTS YOUR EXACT COLUMN NAMES. RUN THE CODE ONCE TO SEE THIS LIST ---
        print("✅ FILE LOADED! AVAILABLE COLUMNS ARE:")
        print(list(df_raw.columns))
        print("-" * 50)

    except Exception as e:
        print(f"❌ Error loading Excel file from URL: {e}")
        return

    # --- 3. EDIT THE LIST BELOW TO MATCH THE COLUMN NAMES PRINTED ABOVE ---
    required_keys = [
        'room type', 'neighbourhood group', 'price', 'Construction year',
        'host name', 'host_identity_verified', 'number of reviews', 'service fee'
    ]

    # Select only the columns that exist in the file
    existing_keys_in_file = [key for key in required_keys if key in df_raw.columns]

    # Create a standardized name (e.g., 'Construction year' -> 'construction_year')
    rename_map = {key: key.lower().replace(' ', '_') for key in existing_keys_in_file}

    df_renamed = df_raw.rename(columns=rename_map)
    df_filtered = df_renamed[list(rename_map.values())] # Use only the renamed columns

    print(f"✅ Keeping and standardizing {len(existing_keys_in_file)} relevant columns.")

    # The rest of the script now uses the cleaned, standardized DataFrame
    df_cleaned = clean_data(df_filtered.copy())

    if not df_cleaned.empty:
        print("\n--- Starting Analysis ---")
        # All plotting functions are called with standardized names
        plot_q1_property_types(df_cleaned)
        plot_q2_top_neighborhoods(df_cleaned)
        plot_q3_avg_price_by_neighborhood(df_cleaned)
        plot_q4_year_vs_price(df_cleaned)
        plot_q5_top_hosts(df_cleaned)
        plot_q6_verified_vs_reviews(df_cleaned)
        plot_q7_price_vs_fee(df_cleaned)
        print("\n--- Analysis Complete ---")

if __name__ == "__main__":
    main()

✅ FILE LOADED! AVAILABLE COLUMNS ARE:
['id', 'NAME', 'host id', 'host_identity_verified', 'host name', 'neighbourhood group', 'neighbourhood', 'lat', 'long', 'country', 'country code', 'instant_bookable', 'cancellation_policy', 'room type', 'Construction year', 'price', 'service fee', 'minimum nights', 'number of reviews', 'last review', 'reviews per month', 'review rate number', 'calculated host listings count', 'availability 365', 'house_rules', 'license']
--------------------------------------------------
✅ Keeping and standardizing 8 relevant columns.
✅ Data cleaning complete.

--- Starting Analysis ---


Analyzing 100619 listings for Question 4...


The correlation between price and service fee is: 1.00



--- Analysis Complete ---
